# Øvingsforelesning 9 - TDT4110

## Eksamen høst 2017, oppgave 3

Vi skal lage programvare for to fotobokser (fotoboks A og fotoboks B) som blant skal brukes til å måle gjennomsnittsfart på kjøretøy. 

<img src="../../Resources/Images/fotoboks.png" style="width: 300px">

Hver fotoboks gjenkjenner registreringsnummer, dato (år, måned, dag) og tidspunkt (timer, minutter, sekund) for alle biler som passerer i en retning (først fotoboks A, deretter fotoboks B)

Målinger fra en fotoboks lagres i en 2-dimensjonal liste på følgende format (her for boks A):

```
box_a= [ 
  [2017, 11, 17, 6, 21, 12, 'HB69082'], 
  [2017, 11, 17, 6, 21, 53, 'CV86023'], 
  ... ,  
  [2017, 11, 17, 6, 23, 0, 'HD27560']
]
```

In [14]:
box_a = [
    [2017, 11, 17, 6, 21, 12, "HB69082"],
    [2017, 11, 17, 6, 21, 53, "CV86023"],
    [2017, 11, 17, 6, 23, 0, "HD27560"],
    [2017, 11, 17, 6, 23, 2, "UT29891"],
    [2017, 11, 17, 6, 24, 25, "IS11293"],
    [2017, 11, 17, 6, 24, 40, "EL73840"],
    [2017, 11, 17, 6, 24, 41, "UT55227"],
    [2017, 11, 17, 6, 26, 55, "NB59108"],
    [2017, 11, 17, 6, 27, 29, "UT46408"],
    [2017, 11, 17, 6, 28, 19, "LE68228"],
]

### Oppgave 3b)

Skriv funksjonen ```time_diff``` som tar inn to lister (```start``` og ```end```), der hver liste beskriver et tidspunkt angitt med dato og klokkeslett. Den første lista (```start```) er tidspunktet for passering av fotoboks A, mens den andre liste (```end```) er tidspunkt for passering av fotoboks B (senere tidspunkt enn A). **Funksjonen skal returnere differansen mellom tidspunktene angitt i sekunder.** 

Funksjonen skal også fungere for forskjellige datoer for å ta hensyn til kjøring rundt midnatt. For å beregne antall dager mellom datoer, kan du bruke funksjonen ```diff_date(d1,d2)``` som returnerer antall dager mellom ```d2``` og ```d1```, der ```d1``` og ```d2``` er dato spesifisert som ei liste på formatet *[y,m,d]*, for eksempel *[2017,11,17]*.

**Eksempel på kjøring:**
```
>>> diff = time_diff([2017,11,17,6,24,40],[2017,11,17,6,32,40])
>>> print(diff) 
480
>>> diff = time_diff([2017,11,17,23,59,59],[2017,11,18,0,9,12])
>>> print(diff)
553
```

#### FORKLARING AV LØSNING

Denne oppgaven kan se ganske vanskelig ut så jeg prøver meg på å legge ved en tekstlig forklaring av løsningen under. Tanken her er først (i motsetning til det jeg gjorde i forelesning) å se på forskjell i klokkeslett. La oss ta noen eksempler:

06:20:00 - 06:21:00 = 60 sekunder
18:21:32 - 18:22:33 = 61 sekunder

Disse to er relatit enkle, for her kan vi bare ta `end - start` for hvert felt, altså f. eks. `end_minutt - start_minutt = 21 - 20 = 1` -> `60 sekunder`. Men hva skjer om et felt i `end` er mindre enn tilsvarende felt i `start`? La oss ta et eksempel til:

06:20:05 - 06:21:00 = 55 sekunder

Hvordan kan vi tenke på dette? La oss se på verdiene for de ulike feltene:
 - Time: `06 - 06 = 0` -> `0 sekunder`
 - Minutt: `21 - 20 = 1` -> `60 sekunder`
 - Sekund: `00 - 05 = -5` -> `-5 sekunder`

Om vi tar summen av disse får vi 55, som er riktig svar! Dette er tankegangen som er benyttet gjennom hele løsningen av oppgaven under, hvor vi starter med den største enheten, og beveger oss til nærmeste "hele" av den, f. eks. når vi sjekker datoforskjeller beveger vi oss kun i steg på størrelse med en dag. Vi utnytter da at tidsforskjellen mellom klokkesletten er negative når `end` er mindre enn `start`, og dermed kan vi bevege oss bakover i tid mot løsningen:

18:20:05 - 18:15:30 = -275 sekunder

```python
timestamp_diff = diff_date(start_date, end_date) * DAYS_TO_SECONDS
```

Deretter beveger vi oss til neste enhet, som er timer, og regner ut forskjellen her. Legg merke til at dersom timeverdien i `end` er lavere enn i `start` vil vi få et negativt tall, og dermed bevege oss "bakover" i tid mot løsningen:

```python
timestamp_diff += (end[3] - start[3]) * HOURS_TO_SECONDS
```

Vi gjentar samme steget for minutter og sekunder, og finner dermed svaret.

Håper denne forklaringen hjelper!

In [1]:
from datetime import datetime

MINUTES_TO_SECONDS = 60
HOURS_TO_SECONDS = 60 * MINUTES_TO_SECONDS
DAYS_TO_SECONDS = 24 * HOURS_TO_SECONDS


# Utdelt funksjon. Denne kan du bruke til å løse oppgave 3b.
def diff_date(d1, d2):
    d1 = datetime(d1[0], d1[1], d1[2])
    d2 = datetime(d2[0], d2[1], d2[2])
    return (d2 - d1).days

def time_diff(start, end):
    start_date = start[:3]
    end_date = end[:3]

    timestamp_diff = diff_date(start_date, end_date) * DAYS_TO_SECONDS
    timestamp_diff += (end[3] - start[3]) * HOURS_TO_SECONDS
    timestamp_diff += (end[4] - start[4]) * MINUTES_TO_SECONDS
    timestamp_diff += end[5] - start[5]
    return timestamp_diff


# Din kode her
print(time_diff([2017, 11, 17, 6, 24, 40], [2017, 11, 17, 6, 32, 40]))
print(time_diff([2017,11,17,23,59,59],[2017,11,18,0,9,12]))

480
553


In [13]:
# test koden din her
diff = time_diff([2017, 11, 17, 6, 24, 40], [2017, 11, 17, 6, 32, 40])
print(diff)  # 480

diff = time_diff([2017, 11, 17, 23, 59, 59], [2017, 11, 18, 0, 9, 12])
print(diff)  # 553

480
553


### Oppgave 3c)

Skriv funksjonen ```check_min_distance``` som har parameterne ```car_table``` og ```diff```. Parameteren ```car_table``` er en todimensjonal tabell av passeringer som spesifisert i introduksjonen, mens ```diff``` er avstand som kreves mellom biler angitt i sekunder. 

**Funksjonen skal returnere registreringsnummer på biler som har mindre avstand i sekunder til bilen foran enn ```diff```.**

Eksempel på kall av funksjonen ```check_min_distance``` med passeringer fra fotoboks A og for avstand mellom biler på mindre enn 3 sekunder:
```
>>> car_table=file_to_table('box_a.txt')
>>> crazy_drivers=check_min_distance(car_table,3) 
>>> print(crazy_drivers)
['UT29891', 'UT55227']
```

In [15]:
def check_min_distance(car_table, diff):
    regnr = []

    for i in range(len(car_table) - 1):
        prev_car = car_table[i]
        next_car = car_table[i + 1]
        if time_diff(prev_car[:-1], next_car[:-1]) < diff:
            regnr.append(next_car[-1])

    return regnr

In [16]:
# test koden din her
crazy_drivers = check_min_distance(box_a, 3)
print(crazy_drivers)  # ['UT29891',  'UT55227']

['UT29891', 'UT55227']


### Oppgave 3d)

Skriv funksjonen ```list_el_cars``` som har en parameter ```car_table``` som er en **todimensjonal tabell av passeringer** slik som spesifisert i introduksjonen. 

**Funksjonen skal returnere antall el-biler som har passert.**

El-biler har registreringsnummer som starter med EK, EL eller EV.

Eksempel på kall av funksjonen ```list_el_cars``` med passeringer fra fotoboks A:
```
>>> el_cars=list_el_cars(car_table)
>>> print(el_cars)
1
```


In [ ]:
# Din kode her

In [ ]:
# test koden din her
el_cars = list_el_cars(box_a)
print(el_cars)  # 1

### Oppgave 3e)

Skriv funksjonen ```generate_license_numbers``` som har en parameter ```amount```. Denne funksjonen skal **returnere ei liste av ```amount``` antall unike vilkårlige registreringsnummer** som kan brukes til testing av systemet. 

Bokstavene i registreringsnummeret kan være en av følgende: 
* BS, CV, EL, FY, KU, LE, NB, PC, SY, WC

Tallet i registreringsnummeret skal være mellom **10000** og **99999.**

Eksempel på kall av funksjonen ```generate_license_numbers```:

```
>>> cars=generate_license_numbers(10)
>>> print(cars)
['CV29728', 'KU73709', 'EL87605', 'NB76581', 'KU65980', 
'WC71086', 'PC48338', 'KU36868', 'NB44194', 'KU10621']
```

In [17]:
import random

LETTERS = ["BS", "CV", "EL", "FY", "KU", "LE", "NB", "PC", "SY", "WC"]

def generate_license_numbers(amount):
    regnr = set()

    while len(regnr) < amount:
        gen = random.choice(LETTERS) + str(random.randint(10000, 99999))
        regnr.add(gen)
    
    return list(regnr)


In [20]:
# test koden din her
cars = generate_license_numbers(10)
print(cars)

my_list = [1, 1, 2, 3, 3]
print(my_list)
print(list(set(my_list)))

['WC55608', 'CV17255', 'SY41304', 'FY48025', 'WC75484', 'WC97942', 'CV87823', 'PC43316', 'FY87112', 'PC27087']
[1, 1, 2, 3, 3]
[1, 2, 3]


### Oppgave 3f)

Skriv funksjonen ```list_speeders``` som har fire parameterere ```lst_A```, ```lst_B```, ```speed_limit``` og ```distance```. De to første parameterne er tabeller som inneholder passeringer for fotoboks A og B. Parameteren ```speed_limit``` angir fartsgrensen for strekningen oppgitt i km/t, mens parameteren ```distance``` oppgir avstand mellom fotoboksene angitt i km. 

**Funksjonen skal returnere en liste av registreringsnummer til alle biler som har kjørt over fartsgrensa (```speed_limit```) for angitt strekning (```distance```).** Det vil i praksis si at funksjonen skal liste opp registreringsnummer til alle **biler som har brukt for kort tid mellom fotoboksene**.

Eksempel på kall av funksjonen ```list_speeders``` med tabellene som beskrevet i introduksjonen, med fartsgrense 60km/t og distanse på 10km:

```
>>> speeders = list_speeders('box_a','box_b',60,10) 
>>> print(speeders)
['UT29891', 'EL73840', 'LE68228']
```


In [ ]:
# Din kode her

## Eksamen høst 2019 (09:00-15:00) Oppgave 3
### Oppgave 3b
Kvar båt har lagra fisken i ei todimensjonal liste. Det kan vere fint å finne ut kor mykje av ein enkelt fiskeart som er lagra. Her kan vi ta for gitt at lagra fisk for ein gitt fiskar er tilgjengeleg gjennom parameteren `store`, mens fisketypen er ein streng gitt i parameteren `kind`. 
Viss det ikkje finst noko fisk av denne typen skal funksjonen returnere talet **0**.

Skriv funksjonen `fish_amount` som tek parameterane `store` og `kind`.

In [ ]:
store = [["torsk", 200], ["sei", 100]]

In [ ]:
# Din kode her

In [ ]:
# test koden din her
torsk_amount = fish_amount(store, "torsk")
print(torsk_amount)  # 200
flygefisk_amount = fish_amount(store, "flygefisk")
print(flygefisk_amount)  # 0

### Oppgave 3c
Lageret skal oppdaterast når det kjem inn meir fisk. Dette vert oppgitt som ei liste med fiskeslag og talet på kilo: `['torsk', 200]`. Lag eit nytt element viss fisketypen ikkje allereie finst i lageret.
Skriv funksjonen `add_fish`, som tar `store` og ei liste som inputparameterar og returnerer det oppdaterte lageret.

In [ ]:
# Din kode her

In [ ]:
# test koden din her
print(store)  # [['torsk', 200], ['sei', 100]]
add_fish(store, ["torsk", 100])
add_fish(store, ["hyse", 70])
print(store)  # [['torsk', 300], ['sei', 100], ['hyse', 70]]

## Eksamen kont 2020 (TDT4109) Oppgave 2
### Oppgave 2.4
Lag funksjonen `calculate` som har ingen inn-parametere, men som skal be brukeren om å skrive inn et regnestykke som kun kan inneholde tall, + og -. Funksjonen skal ta hensyn til at man kan skrive desimaltall både med desimalkomma og desimalpunktum. Det må også tas hensyn til at det kan skrives åpenrom (mellomrom) i uttrykket. Løsningen kan ikke benytte seg av den innebygde funksjon eval() eller lignende.
Funksjonen skal først spørre brukeren: "Enter calculation" - der brukeren skal skrive inn et regnestykke. Funksjonen beregne svaret og skrive ut svaret til konsollet etter teksten: "Result: "

In [27]:
def calculate():
    expression = input("Enter calculation: ")
    expression = expression.replace(",", ".").replace(" ", "")

    parts = expression.split("+")
    result = 0

    for part in parts:
        # part = 3 - 2.5 - 2 -> ["3", "2.5", "2"]
        # part = 3 -> ["3"]
        # part = 3 - 2.5
        subparts = part.split("-")
        result += float(subparts[0])
        for subpart in subparts[1:]:
            result -= float(subpart)

    print(f"Result: {result}")

In [28]:
# test koden din her
calculate()

Result: 2.5


### Oppgave 3.2
Lag funksjonen `time_to_sec` som tar inn en input-parameter tstring som er en streng med tidsinformasjon spesifisert som "time:minutt:sekund" og regner den om til antall sekunder. Det er ikke gitt at alle elementene er med. Funksjonen må håndtere strenger som "30","20:30","1:20:30","1::30","::45",":12:","1::".
Funksjonen behøver ikke ta hensyn til strenger som ikke følger dette formatet. Funksjonen skal returnere antall sekunder strengen representerer som et heltall.

In [30]:
def parse_int_safely(string):
    if string == "":
        return 0
    return int(string)

def time_to_sec(tstring):
    parts = tstring.split(":")
    result = parse_int_safely(parts[-1])

    if len(parts) >= 2:
        result += parse_int_safely(parts[-2]) * MINUTES_TO_SECONDS

    if len(parts) == 3:
        result += parse_int_safely(parts[-3]) * HOURS_TO_SECONDS
    
    return result


In [35]:
# test koden din her
sec = time_to_sec("2:03:04")
print(sec)  # 7384

4


## Eksamen høst 2020 (TDT4109) Oppgave 2
### Oppgave 2.1 
Lag funksjonen `check_across_div` som har to input-parametere `num1` og `num2`, som begge er heltall. Funksjonen skal sjekke om tverrsummen av num1 er delelig med num2.
Tverrsummen av et tall finner man ved at man summerer sifferne i tallet: Tverrsummen av 123 = 1 + 2 + 3 = 6, og tverrsummen av 255 = 2 + 5 + 5 = 12
Funksjonen skal returnere `True` hvis tverrsummen av num1 er delelig med num2. Hvis ikke, skal `False` returneres.

In [38]:
def check_across_div(num1, num2):
    tverrsum = 0
    for siffer in str(num1):
        tverrsum += int(siffer)
    
    return tverrsum % num2 == 0

In [39]:
# test koden din her
print(check_across_div(123, 6))  # True
print(check_across_div(10, 10))  # False
print(check_across_div(243, 3))  # True

True
False
True


### Oppgave 2.2
Lag funksjonen `pick_num_string` som har en input-parameter `txt` som er en tekststreng som kan bestå av både bokstaver og tall.
Funksjonen skal returnere alle tallene som ble funnet i tekststrengen som en liste i stigende rekkefølge. Lista skal ikke ha duplikater av samme tall hvis man finner tallet flere ganger i txt.
Funksjonen kan testes med følgende argument: `txt='948ugj23dsfh34hgf834nsd321395j'`

In [ ]:
# test koden din her
liste = pick_num_string("948ugj23dsfh34hgf834nsd321395j")
print(liste)  # [1, 2, 3, 4, 5, 8, 9]

## Eksamen høst 2020 (TDT4109) Oppgave 3
### Oppgave 3.1 
Vi representerer internt hvert kort **[i en kortstokk]** som et 2-tuppel: `(v,f)`.
Her er v et tall fra 2 til 14 (14 er ess), og f er et av tegnene **'s','h','d','c'**,
for henholdsvis spar (spades), hjerter (hearts), ruter (diamonds) og kløver (clubs).

a) Skriv funksjonen `new_deck` uten input-parametre, som returnerer en liste med alle 52 kort, representert som tupler beskrevet over. Rekkefølgen spiller ingen rolle.

b) Skriv funksjonen `shuffle` som tar en input-parameter liste, som er en liste (muterbar sekvens). Den skal returnere en liste med de samme elementene, men i en annen og tilfeldig rekkefølge.

In [ ]:
# Din kode her

In [ ]:
# test koden din her
deck = new_deck()
print(deck)

In [ ]:
print(shuffle(deck))